In [1]:
from library_functions.imports_explainer_notebook import *

# Comunity Detection and Categorization

One of the things we were curious about as we started this project was wether community-detection algorithms woould be able to pick up communities that correspond to actual, known, categorizations of our nodes.

The results of our exploration can be found in an interactive form on our website, [TODO] so instead of repeating everything here, we'll simply describe our attempts at community detection, the problems we encountered, and what we ended up using.

Before we start, let's load in our networks - note that for this part, we only look at the undirected version of the WikiPedia network, and we look only at the Largest Connected Component.

In [2]:
graph_reddit = w.graph.largest_connected_component(
    lf.create_graph_reddit(
        max_drugs_in_post=6,
        min_edge_occurrences_to_link=2,
        min_content_length_in_characters=25
    )
)
graph_wiki = w.graph.largest_connected_component(lf.create_graph_wiki().to_undirected())


## Laying out the networks: ForceAtlas 2 all over again

To be able to visualize any communities we might find, we first needed to compute a good layout for our graph. We instantiated the algorithm with the following parameters:

In [4]:
forceatlas2 = ForceAtlas2(
    # Behavior alternatives
    outboundAttractionDistribution=True,  # Dissuade hubs
    edgeWeightInfluence=1.0,
    # Performance
    jitterTolerance=0.5,  # Tolerance
    barnesHutOptimize=True,
    barnesHutTheta=1.2,
    # Tuning
    scalingRatio=5,
    strongGravityMode=False,
    gravity=1,
    # Log
    verbose=True,
)

NameError: name 'ForceAtlas2' is not defined

For the wikipedia network, this worked pretty well out of the box.

As an aside, note that the network visualizations in this section are interactive - we implemented some functions that allow us to visualize a graph with [Plotly](https://plotly.com), and to get information about nodes when hovering them.

In [8]:
positions_wiki = lf.get_fa2_layout(graph=graph_wiki)
wiki_graph_plot = lf.draw_graph_plotly(
    graph=graph_wiki,
    positions=positions_wiki,
    node_size_attribute="degree",  # Size nodes by degree
)
wiki_graph_plot

100%|██████████| 1000/1000 [00:07<00:00, 130.49it/s]
BarnesHut Approximation  took  3.08  seconds
Repulsion forces  took  4.01  seconds
Gravitational forces  took  0.04  seconds
Attraction forces  took  0.03  seconds
AdjustSpeedAndApplyForces step  took  0.27  seconds


In [ ]:
For the reddit graph, however, the results were underwhelming:

In [12]:
positions_reddit = lf.get_fa2_layout(graph=graph_reddit)
reddit_graph_plot = lf.draw_graph_plotly(
    graph=graph_reddit,
    positions=positions_reddit,
    node_size_attribute="degree",  # Size nodes by degree
    edge_weight_attribute="count" # Size edges by how ofter the link appears
)
reddit_graph_plot

100%|██████████| 1000/1000 [00:01<00:00, 501.56it/s]
BarnesHut Approximation  took  0.51  seconds
Repulsion forces  took  1.29  seconds
Gravitational forces  took  0.01  seconds
Attraction forces  took  0.03  seconds
AdjustSpeedAndApplyForces step  took  0.08  seconds


We attempted to let the ForceAtlas2 algorithm use the weight of the edges (the 'count' attribute) to draw a better layout, but the results weren't so much better, other than bringing the most central nodes to the center (note that we had to install the latest version of ForceAtlas2 from github for this to work, as the one on PIP does not have this functionality):

In [5]:
positions_reddit_weighted = lf.get_fa2_layout(
    graph=graph_reddit,
    edge_weight_attribute="count"
)
reddit_graph_plot_weighted = lf.draw_graph_plotly(
    graph=graph_reddit,
    positions=positions_reddit_weighted,
    node_size_attribute="degree",  # Size nodes by degree
    edge_weight_attribute="count" # Size edges by how ofter the link appears
)
reddit_graph_plot_weighted

100%|██████████| 1000/1000 [00:02<00:00, 401.90it/s]
BarnesHut Approximation  took  0.59  seconds
Repulsion forces  took  1.69  seconds
Gravitational forces  took  0.01  seconds
Attraction forces  took  0.03  seconds
AdjustSpeedAndApplyForces step  took  0.09  seconds


We tried a few more things, but unfortunately, the python version of the FA2  algorithm is very limited. Which is a pity, because the version of ForceAtlas2 on Gephi implements a lin-log mode that makes it possible to get a very nice layout for the same graph:

![](https://github.com/wojciechdk/Social_Graphs_and_Interactions_Final_Project/raw/master/explainer_notebook/gephi_layout.png)


Maybe implementing the lin-log mode in python could be a project idea for future iterations of this course? ;-)

## Good old Louvain

As we had used it during class, for our first attempt at community detection, we tried to apply the Louvain algorithm to both networks. 
For the WikiPedia network, it gave rather good results out-of-the box - and the resulting communities were clearly identifiable when coloring our nodes by community.

Note that we are including screenshots from our website: plotly was exceedingly slow for coloring nodes with different colors (and when more than a couple of plots were displayed on the same page), so we resorted to yet another library, [Cytoscape.js](https://js.cytoscape.org) - however, being a javascript library, it only works reliably in the browser. Please go view these plots on our website for the best experience.

![](https://github.com/wojciechdk/Social_Graphs_and_Interactions_Final_Project/raw/master/explainer_notebook/louvain_wiki.png)



*(Extra note: since the FA2 algorithm is nondeterministic, and the graph above was generated on the website rather than when we created this notebook, the layout looks slightly different - but you get the idea.)*

For the reddit graph, we were afraid that the algorithm would have trouble finding communities due to the highly connected nature of that network. However, it looks like the results are satisfactory - even on our "hairball" graph, the communities are quite well spatially separated:

![](https://github.com/wojciechdk/Social_Graphs_and_Interactions_Final_Project/raw/master/explainer_notebook/louvain_reddit_coarse.png)

To be able to compare communities to categories on a more granular level, we also increased the granularity of the louvain algorithm - resulting in more, and smaller,  communities:

![](https://github.com/wojciechdk/Social_Graphs_and_Interactions_Final_Project/raw/master/explainer_notebook/louvain_reddit_fine.png)

For the answers to our initial question, and a comparison of the detected communities with the categories on both wikipedia and reddit, please see our website - it isn't really interesting to repeat it here.m